# Parsing PDF with docling

In [1]:
import json
import time
from pathlib import Path

from docling.datamodel.base_models import InputFormat
from docling.datamodel.pipeline_options import (
PdfPipelineOptions,
)
from docling.document_converter import DocumentConverter, PdfFormatOption

input_doc_path = "./data/chapter02-05.pdf"

# Docling Parse without EasyOCR
# -------------------------
pipeline_options = PdfPipelineOptions()
pipeline_options.do_ocr = False
pipeline_options.do_table_structure = True
pipeline_options.table_structure_options.do_cell_matching = True

doc_converter = DocumentConverter(
    format_options={
        InputFormat.PDF: PdfFormatOption(pipeline_options=pipeline_options)
    }
)

###########################################################################

start_time = time.time()
conv_result = doc_converter.convert(input_doc_path)
end_time = time.time() - start_time

print(f"Document converted in {end_time:.2f} seconds.")

## Export results
output_dir = Path("scratch-docling-parse")
output_dir.mkdir(parents=True, exist_ok=True)
doc_filename = conv_result.input.file.stem

# Export Docling document JSON format:
with (output_dir / f"{doc_filename}.json").open("w", encoding="utf-8") as fp:
    fp.write(json.dumps(conv_result.document.export_to_dict(), indent=2, ensure_ascii=False))

# Export Markdown format:
with (output_dir / f"{doc_filename}.md").open("w", encoding="utf-8") as fp:
    fp.write(conv_result.document.export_to_markdown())

# Export Document Tags format:
with (output_dir / f"{doc_filename}.doctags").open("w", encoding="utf-8") as fp:
    fp.write(conv_result.document.export_to_doctags())

2025-10-31 09:11:50,493 - INFO - detected formats: [<InputFormat.PDF: 'pdf'>]
2025-10-31 09:11:50,530 - INFO - Going to convert document batch...
2025-10-31 09:11:50,531 - INFO - Initializing pipeline for StandardPdfPipeline with options hash 75463f421d05cb4304e1f714cf00d35d
2025-10-31 09:11:50,546 - INFO - Loading plugin 'docling_defaults'
2025-10-31 09:11:50,548 - INFO - Registered picture descriptions: ['vlm', 'api']
2025-10-31 09:11:50,562 - INFO - Loading plugin 'docling_defaults'
2025-10-31 09:11:50,566 - INFO - Registered ocr engines: ['auto', 'easyocr', 'ocrmac', 'rapidocr', 'tesserocr', 'tesseract']
2025-10-31 09:11:50,597 - INFO - Accelerator device: 'cuda:0'
2025-10-31 09:11:53,086 - INFO - Accelerator device: 'cuda:0'
2025-10-31 09:11:54,441 - INFO - Processing document chapter02-05.pdf
2025-10-31 09:13:01,317 - INFO - Finished converting document chapter02-05.pdf in 70.83 sec.


Document converted in 70.83 seconds.


In [2]:
import pickle

# checkpoint
with open('checkpoints/chapter02-04-doclingdoc.pkl', 'wb') as file:
    pickle.dump(conv_result.document, file)

# Normalizing text

In [23]:
import pickle

# read from checkpoitn
with open('checkpoints/chapter02-04-doclingdoc.pkl', 'rb') as file:
    docling_document = pickle.load(file)


In [ ]:
!pip install -q shekar

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [24]:
import os
# https://github.com/huggingface/transformers/issues/5486:
os.environ["TOKENIZERS_PARALLELISM"] = "false"

In [25]:
from  shekar import Normalizer
import re

def fix_persian_numbers(s: str) -> str:
    # Match sequences of Persian digits
    pattern = re.compile(r"[۰-۹]+")
    
    def reverse_num(match):
        num = match.group(0)
        return num[::-1]  # reverse characters
    
    return pattern.sub(reverse_num, s)

normalizer = Normalizer()
for text in docling_document.texts:
    text.orig = fix_persian_numbers(normalizer(text.orig))
    text.text = fix_persian_numbers(normalizer(text.text))

# Chunking

In [26]:
from docling.chunking import HybridChunker

chunker = HybridChunker(tokenizer="google/gemma-3-12b-it", max_tokens=250)
chunks = chunker.chunk(docling_document)
chunks = list(chunks)
len(chunks)

/home/user/.pyenv/versions/user/lib/python3.11/site-packages/docling_core/transforms/chunker/hybrid_chunker.py:235: UserWarning: Headers and captions for this chunk are longer than the total available size for the chunk, so they will be ignored: doc_chunk.text='ج- به منظور حذف الزاماتی که مانع از اجرای سیاست چابک سازی، منطقی سازی و متناسب سازی دستگاه\u200cهای اجرایی و موجب گسترش بی\u200cرویه ساختارهای سازمانی شدهاند، بخشنامه\u200cهای زیر که از سوی این معاونت ابلاغ شده، لغو می. شود ۱بند های ۱۵ و ۱۶ جدول شماره ۲ پیوست بخشنامه شماره ۳۶۲۷۱ / ۲۰۰ مورخ ۱۳ / ۰۷ / ۱۳۸۹، همچنین، بخشنامه شماره ۸۶۴۳۱ / ۲۰۰ مورخ ۱۱ / ۹ / ۱۳۸۸ این معاونت موضوع ایجاد پست\u200cهای قائم\u200cمقام وزیر در امور همکاریهای بین\u200cالمللی و قائم\u200cمقام وزیر در امور ارتباطات مردمی. ۲- بخشنامه شماره ۵۱۸۰۵ / ۲۰۰ مورخ ۸ / ۱۰ / ۱۳۸۹ این معاونت موضوع ایجاد حوزه مشاوران جوان در نهاد ریاست جمهوری و ایجاد پست مشاور جوان در وزارتخانه\u200cها و سازمان\u200cهای مستقل و استانداری\u200cها. ۳- بخشنامه شماره ۵۴۹۸۹ / ۲۰۰ مورخ ۲۵ / ۱۰ /

755

In [1]:
import pickle

# checkpoint
with open('checkpoints/chapter02-04-chunks.pkl', 'wb') as file:
    pickle.dump(chunks, file)

FileNotFoundError: [Errno 2] No such file or directory: 'checkpoints/chapter02-04-chunks.pkl'

# Embedding

In [ ]:
# import pickle

# # Now, to read the JSON file back into a Python object
# with open('checkpoints/chapter02-04-chunks.pkl', 'rb') as json_file:
#     chunks = pickle.load(json_file)

In [28]:
import torch
from FlagEmbedding import BGEM3FlagModel
from tqdm.notebook import tqdm

device = "cuda" if torch.cuda.is_available() else "cpu"
print("Using:", device)

model = BGEM3FlagModel('BAAI/bge-m3', use_fp16=True, devices=device)


Using: cuda

Fetching 30 files:   0%|          | 0/30 [00:00<?, ?it/s]

In [29]:
# https://huggingface.co/docs/transformers/model_doc/auto#transformers.AutoTokenizer

from transformers import AutoTokenizer
from huggingface_hub import login
from collections import Counter

tokenizer = AutoTokenizer.from_pretrained("google/gemma-3-12b-it")

# chunks_sizes = []
# for chunk in chunks:
#     chunks_sizes.append(len(tokenizer.tokenize(chunk.text)))

In [30]:
for chunk in chunks:
    if len(tokenizer.tokenize(chunk.text)) < 20 and chunk.meta.doc_items[0].label == "text":
        print(chunker.contextualize(chunk))
        print()

(تصویب نامه شماره ۱۶۳۴۶۴/ت۴۵۰۲۰ک مورخ ۲۲ / ۷/۱۳۸۹ هیأت وزیران با اصلاحات و الحاقات بعدی)
در اختیار مؤسسات مجری قرار دهند، در این صورت:
۳۷

(تصویب نامه شماره ۲۳۶۵۴۱/ت۶۱۰۶۵ه مورخ ۲۱/۱۲/۱۴۰۲ هیئت وزیران)
جمهوری (مر کز ارتباطات مردمی) فراهم نمایند.

نحوه پرداخت حق سنوات قرارداد کارمندان کار معین (بخشنامه شماره ۳۰۰۴ مورخ ۰۴ / ۰۴/۱۴۰۲ سازمان اداری و استخدامی کشور)
حسین عرب اسدی- معاون سرمایه انسانی

(تصویب نامه شماره ۸۰۷۴۶/ت۵۹۵۴۰ه مورخ ۱۲/۵/۱۴۰۱ هیئت وزیران)
روابط‌عمومی دستگاه‌ها
نشر اداری‌ها
۶۷۱

الف- مؤسسات آموزشی
(ماده ۱۶) قانون مدیریت خدمات کشوری بلامانع است.

...

(جدول شماره ۳): فضای اصلی اداری مورد نیاز مدیران حرفه‌ای، کارشناسان و کارمندان در سطح شهرستان
۲۶ مترمربع فضای اصلی اداری مورد نیاز مشاوران وزرا

(مصوبه شماره ۱۰۲۳۵۳ مورخ ۵ / ۳/۱۳۹۷ شورای عالی اداری)
نشر اداری‌ها
۲۵۲

(بخشنامه شماره ۲۴۷۹۱۸ مورخ ۱۸/۵/۱۳۹۷ سازمان اداری و استخدامی کشور)
اتمام طرح‌های نیمه‌تمام و اجرای طرح‌های تحول اداری اقدام نمایند.

(تصویب نامه شماره ۸۱۸۳۹/ت۴۴۲۹۴ک مورخ ۱۹/۴/۱۳۹۰ هیئت وزیران)
آمار ایران.
۶۵۲

فصل دوم) فرآیند ثبت اطلاعات در زیرسامانه‌های سامانه‌یکپارچه نظام اداری (سینا)
). (راهنمای تصویری این فصل به پیوست بخشنامه قابل مشاهده می‌باشد

In [31]:
# Assuming chunks is a list of dictionaries
CHUNK_SIZE_LIMIT = 20
chunks = [chunk for chunk in chunks if len(tokenizer.tokenize(chunk.text)) > CHUNK_SIZE_LIMIT and chunk.meta.doc_items[0].label == "text"]

In [14]:
len(chunks)

639

In [32]:
# Example: chunks = [...]  # Your list of dicts loaded earlier
texts = [c.text for c in chunks]

In [33]:
print("Embedding chunks...")
import numpy as np

embeddings = model.encode(
    texts,
    return_dense=True,
    return_sparse=True,
    return_colbert_vecs=True,
    batch_size=16,
    max_length=512,
)

dense_vectors = np.array(embeddings["dense_vecs"], dtype=np.float32)
sparse_vectors = embeddings["lexical_weights"]  # scipy.sparse.csr_matrix

print("Done ✅")


Embedding chunks...

pre tokenize: 100%|██████████| 40/40 [00:00<00:00, 97.28it/s]
You're using a XLMRobertaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.
Inference Embeddings: 100%|██████████| 40/40 [00:02<00:00, 19.81it/s]


Done ✅

In [17]:
import pickle

# checkpoint
with open('checkpoints/embeddings-bge-m3.pkl', 'wb') as file:
    pickle.dump(embeddings, file)

# Retreival

In [34]:
import pickle
import numpy as np

# read from checkpoint
# with open('checkpoints/embeddings-bge-m3.pkl', 'rb') as file:
#     embeddings = pickle.load(file)

dense_vectors = np.array(embeddings["dense_vecs"], dtype=np.float32)
sparse_vectors = embeddings["lexical_weights"]  # scipy.sparse.csr_matrix

In [49]:
with open('checkpoints/clean_chunks.pkl', 'wb') as file:
    pickle.dump(chunks, file)

In [19]:
embeddings

{'dense_vecs': array([[ 0.01131  ,  0.02258  ,  0.02101  , ...,  0.003475 , -0.0383   ,
          0.007477 ],
        [-0.00756  ,  0.01842  ,  0.02678  , ..., -0.01678  , -0.01942  ,
         -0.00736  ],
        [-0.0002164, -0.003395 ,  0.000597 , ..., -0.0091   , -0.0675   ,
         -0.0368   ],
        ...,
        [-0.0634   , -0.009    , -0.01765  , ...,  0.007633 , -0.04935  ,
         -0.01394  ],
        [-0.02493  ,  0.01738  , -0.01643  , ..., -0.02248  , -0.07874  ,
         -0.063    ],
        [-0.00525  ,  0.0308   , -0.02425  , ..., -0.00778  , -0.07043  ,
         -0.02719  ]], shape=(639, 1024), dtype=float16),
 'lexical_weights': [defaultdict(int,
              {'54754': np.float16(0.1525),
               '26468': np.float16(0.254),
               '258': np.float16(0.0587),
               '71471': np.float16(0.2417),
               '746': np.float16(0.1243),
               '35934': np.float16(0.265),
               '140': np.float16(0.1904),
               '584': n

In [20]:
dense_vectors.shape

(639, 1024)

In [21]:
sparse_vectors

[defaultdict(int,
             {'54754': np.float16(0.1525),
              '26468': np.float16(0.254),
              '258': np.float16(0.0587),
              '71471': np.float16(0.2417),
              '746': np.float16(0.1243),
              '35934': np.float16(0.265),
              '140': np.float16(0.1904),
              '584': np.float16(0.1322),
              '14969': np.float16(0.265),
              '27263': np.float16(0.1757),
              '65': np.float16(0.0736),
              '11850': np.float16(0.1985),
              '412': np.float16(0.0593),
              '89606': np.float16(0.05844),
              '27284': np.float16(0.1246),
              '96411': np.float16(0.03052),
              '1287': np.float16(0.0869),
              '35117': np.float16(0.09186),
              '4145': np.float16(0.08215),
              '5150': np.float16(0.01976),
              '69029': np.float16(0.1627),
              '8383': np.float16(0.0687),
              '89107': np.float16(0.175),
         

In [35]:
from sklearn.preprocessing import normalize

# Normalize dense vectors for cosine similarity
dense_vectors = normalize(dense_vectors, axis=1)

In [36]:
from scipy import sparse
import numpy as np

def lexical_to_csr(lexical_weights, vocab_size):
    """
    Convert list[defaultdict] → csr_matrix of shape (num_docs, vocab_size)
    """
    data = []
    rows = []
    cols = []

    for i, word_dict in enumerate(lexical_weights):
        for token_id_str, weight in word_dict.items():
            token_id = int(token_id_str)
            data.append(float(weight))         # convert np.float16 → float
            rows.append(i)
            cols.append(token_id)

    matrix = sparse.csr_matrix((data, (rows, cols)), shape=(len(lexical_weights), vocab_size))
    return matrix

In [37]:
vocab_size = model.tokenizer.vocab_size
sparse_vectors = lexical_to_csr(embeddings["lexical_weights"], vocab_size)

In [38]:
def hybrid_search(query, top_k=5, alpha=0.5):
    """
    alpha = weight for dense similarity (0-1)
    """
    q = model.encode([query], return_dense=True, return_sparse=True)

    # ----- Dense -----
    q_dense = np.array(q["dense_vecs"], dtype=np.float32).reshape(1, -1)
    q_dense = normalize(q_dense, axis=1)
    dense_scores = (dense_vectors @ q_dense.T).squeeze()
    
    # ----- Sparse -----
    q_sparse = lexical_to_csr([q["lexical_weights"][0]], vocab_size)
    sparse_scores = (sparse_vectors @ q_sparse.T).toarray().squeeze()

    # ----- Hybrid Score -----
    scores = alpha * dense_scores + (1 - alpha) * sparse_scores

    # ----- Top-K -----
    top_idx = np.argsort(scores)[::-1][:top_k]
    return [(chunks[i], float(scores[i])) for i in top_idx]


In [39]:
from rich import print 

query = "شرایط عمومی احراز صلاحیت افراد امتیازآور"
results = hybrid_search(query, top_k=5, alpha=0.7)

for i, (chunk, score) in enumerate(results, 1):
    print(f"\n[{i}] score={score:.4f}\n{chunk}")


[1] score=0.6194
text='ماده ۴شرایط عمومی احراز صلاحیت افراد امتیازآور:\n- ۱-۴- تابعیت جمهوری اسلامی ایران را داشته باشد.\n- ۲-۴- 
دارای مدر ک تحصیلی حداقل لیسانس یا معادل آن مرتبط با تخصص و رشته\u200cها تحصیلی مورد نظر طبق جدول شماره ۱ باشد.\n- 
۳-۴- محروم از حقوق اجتماعی موضوع ماده ۲۶ قانون مجازات اسلامی نباشد.\n- ۴-۴- رابطه استخدامی (رسمی، پیمانی، قراردادی 
و عناوین مشابه) با دستگاه\u200cهای اجرایی نداشته باشد.\n- ۴-۵ممنوعیت مداخله در معاملات دولتی، موضوع لایحه قانونی 
راجع به منع مداخله وزرا، نمایندگان مجلس و کارمندان دولت در معاملات دولتی و کشوری نداشته باشد.' 
meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', 
doc_items=[DocItem(self_ref='#/texts/121', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=18, 
bbox=BoundingBox(l=221.57, t=578.301990234375, r=399.939, b=565.4299902343749, 
coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 48))]), DocItem(self_ref='#/texts/122', 
parent=RefItem(cref='#/groups/8'), children=[], content_layer=<ContentLayer.BODY: 'body'>, 
label=<DocItemLabel.LIST_ITEM: 'list_item'>, prov=[ProvenanceItem(page_no=18, bbox=BoundingBox(l=229.61, 
t=558.981990234375, r=399.905, b=546.109990234375, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), 
charspan=(0, 47))]), DocItem(self_ref='#/texts/123', parent=RefItem(cref='#/groups/8'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.LIST_ITEM: 'list_item'>, 
prov=[ProvenanceItem(page_no=18, bbox=BoundingBox(l=54.984, t=539.661990234375, r=399.905, b=510.469990234375, 
coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 113))]), DocItem(self_ref='#/texts/124', 
parent=RefItem(cref='#/groups/8'), children=[], content_layer=<ContentLayer.BODY: 'body'>, 
label=<DocItemLabel.LIST_ITEM: 'list_item'>, prov=[ProvenanceItem(page_no=18, bbox=BoundingBox(l=141.29, 
t=504.021990234375, r=399.905, b=491.14999023437497, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), 
charspan=(0, 68))]), DocItem(self_ref='#/texts/125', parent=RefItem(cref='#/groups/8'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.LIST_ITEM: 'list_item'>, 
prov=[ProvenanceItem(page_no=18, bbox=BoundingBox(l=60.504, t=484.821990234375, r=399.905, b=471.949990234375, 
coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 95))]), DocItem(self_ref='#/texts/126', 
parent=RefItem(cref='#/groups/8'), children=[], content_layer=<ContentLayer.BODY: 'body'>, 
label=<DocItemLabel.LIST_ITEM: 'list_item'>, prov=[ProvenanceItem(page_no=18, bbox=BoundingBox(l=54.984, 
t=465.501990234375, r=399.905, b=436.27999023437496, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), 
charspan=(0, 149))])], headings=['فصل دوم: صلاحیت حرفه\u200cای افراد امتیازآور'], captions=None, 
origin=DocumentOrigin(mimetype='application/pdf', binary_hash=165792075628353383, filename='chapter02-05.pdf', 
uri=None))

[2] score=0.5513
text='تبصره ۱: برای افراد امتیازآور معرفی شده از سوی مراکز آموزشی و پژوهشی دولتی و غیردولتی، داشتن مدر ک تحصیلی 
دکتری با درجه علمی حداقل دانشیار در رشته\u200cهای مرتبط با تخصص و رشته\u200cهای تحصیلی (مندرج در جدول ۱) بخشنامه 
الزامی می\u200cباشد. (الحاقی به موجب بخشنامه شماره ۲۴۲۳۳۹ مورخ ۱۴ / ۵/۱۳۹۹)\nتبصره ۲: رعایت بندهای ۴ -۴ و ۴-۵ برای 
افراد امتیازآور معرفی شده از سوی مراکز دولتی، الزامی نیست. (الحاقی به موجب بخشنامه شماره ۲۴۲۳۳۹ مورخ ۱۴/۵ / 
۱۳۹۹)\nماده ۵شرایط اختصاصی احراز صلاحیت افراد امتیازآور:\n۱-۵- تعیین امتیاز حرفه\u200cای افراد امتیازآور بر اساس 
جدول ۲ و با توجه به پایه و تخصص مورد تقاضا توسط شر کت مورد محاسبه قرار می\u200cگیرد.' 
meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', 
doc_items=[DocItem(self_ref='#/texts/127', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=18, 
bbox=BoundingBox(l=54.984, t=429.831990234375, r=399.981, b=369.629990234375, coord_origin=<CoordOrigin.BOTTOMLEFT:
'BOTTOMLEFT'>), charspan=(0, 293))]), DocItem(self_ref='#/texts/128', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=18, 
bbox=BoundingBox(l=55.104, t=363.111990234375, r=399.932, b=335.429990234375, coord_origin=<CoordOrigin.BOTTOMLEFT:
'BOTTOMLEFT'>), charspan=(0, 155))]), DocItem(self_ref='#/texts/129', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=18, 
bbox=BoundingBox(l=210.29, t=329.031990234375, r=399.939, b=316.159990234375, coord_origin=<CoordOrigin.BOTTOMLEFT:
'BOTTOMLEFT'>), charspan=(0, 50))]), DocItem(self_ref='#/texts/130', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=18, 
bbox=BoundingBox(l=54.984, t=309.711990234375, r=399.905, b=280.499990234375, coord_origin=<CoordOrigin.BOTTOMLEFT:
'BOTTOMLEFT'>), charspan=(0, 132))])], headings=['فصل دوم: صلاحیت حرفه\u200cای افراد امتیازآور'], captions=None, 
origin=DocumentOrigin(mimetype='application/pdf', binary_hash=165792075628353383, filename='chapter02-05.pdf', 
uri=None))

[3] score=0.4756
text='۸-۳- فرد امتیازآور: کارشناسی است که حداقل امتیاز حرفه\u200cای لازم از مندرجات جدول شماره ۲ برای پایه مورد نظر
را کسب نموده و فعالیتهای مرتبط با تخصص مورد تقاضا را با همکاری گروه به عهده\u200cدار د.\n۹-۳- گروه: دربر گیرنده 
افرادی با عناوین سر گروه و امتیازآوران می\u200cباشند که\u200cبرای انجام خدمات مشاوره\u200cای در یک تخصص تشکیل 
شده\u200cاست.\n۱۰-۳سر گروه: کارشناسی که دارای حداقل امتیاز حرفهای لازم از مندرجات جدول شماره ۲ برای پایه مورد نظر و
سایر شرایط لازم بوده و سرپرستی فعالیت\u200cهای مشاوره\u200cای مربوط به تخصص مورد تقاضا را در شر کت برعهده داشته 
باشد.' meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', 
doc_items=[DocItem(self_ref='#/texts/113', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=17, 
bbox=BoundingBox(l=66.504, t=281.611990234375, r=411.305, b=252.41999023437495, 
coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 192))]), DocItem(self_ref='#/texts/114', 
parent=RefItem(cref='#/body'), children=[], content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 
'text'>, prov=[ProvenanceItem(page_no=17, bbox=BoundingBox(l=66.384, t=245.97199023437497, r=411.305, 
b=216.77999023437496, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 129))]), 
DocItem(self_ref='#/texts/115', parent=RefItem(cref='#/body'), children=[], content_layer=<ContentLayer.BODY: 
'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=17, bbox=BoundingBox(l=66.384, 
t=210.33199023437498, r=411.305, b=164.81999023437498, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), 
charspan=(0, 210))])], headings=['ماده ۳تعاریف:'], captions=None, origin=DocumentOrigin(mimetype='application/pdf',
binary_hash=165792075628353383, filename='chapter02-05.pdf', uri=None))

[4] score=0.4545
text='امتیاز مربوط به کیفیت تجربه کاری شرکت متقاضی تشخیص صلاحیت پایه\u200cهای؛ ۱، ۲ و ۳، با اجرای حداقل ۳ پروژه و 
بر اساس رعایت زمان (بندی اجرای هر پروژه ۵ امتیاز)، ارائه خروجی و نتایج اصلی پروژه (۲۵ (امتیاز) و در صورت داشتن 
نوآوری و ابتکار ۲۰ امتیاز) با تأیید سازمان محاسبه می\u200cگردد.\nماده ۱۲شرایط لازم برای تشخیص صلاحیت 
مشاوران:\nحداقل شرایط لازم برای تشخیص صلاحیت مشاوران بر اساس جدول شماره ۳ تعیین می\u200cگردد.\n\n(جدول شماره ۳): 
حداقل شرایط لازم برای تشخیص صلاحیت مشاوران' meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', 
version='1.0.0', doc_items=[DocItem(self_ref='#/texts/149', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=21, 
bbox=BoundingBox(l=66.384, t=526.341990234375, r=411.325, b=480.949990234375, coord_origin=<CoordOrigin.BOTTOMLEFT:
'BOTTOMLEFT'>), charspan=(0, 277))]), DocItem(self_ref='#/texts/150', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=21, 
bbox=BoundingBox(l=226.97, t=474.501990234375, r=411.339, b=461.629990234375, coord_origin=<CoordOrigin.BOTTOMLEFT:
'BOTTOMLEFT'>), charspan=(0, 45))]), DocItem(self_ref='#/texts/151', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=21, 
bbox=BoundingBox(l=104.66, t=455.151990234375, r=411.239, b=442.27999023437496, 
coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 80))]), DocItem(self_ref='#/texts/152', 
parent=RefItem(cref='#/tables/4'), children=[], content_layer=<ContentLayer.BODY: 'body'>, 
label=<DocItemLabel.CAPTION: 'caption'>, prov=[ProvenanceItem(page_no=21, bbox=BoundingBox(l=115.34, 
t=435.831990234375, r=364.094, b=422.95999023437497, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), 
charspan=(0, 59))]), TableItem(self_ref='#/tables/4', parent=RefItem(cref='#/body'), 
children=[RefItem(cref='#/texts/152')], content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TABLE: 
'table'>, prov=[ProvenanceItem(page_no=21, bbox=BoundingBox(l=67.33781433105469, t=421.0943298339844, 
r=412.3470764160156, b=93.3319091796875, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 0))], 
captions=[RefItem(cref='#/texts/152')], references=[], footnotes=[], image=None, 
data=TableData(table_cells=[TableCell(bbox=BoundingBox(l=394.3, t=279.596, r=405.321, b=291.21000000000004, 
coord_origin=<CoordOrigin.TOPLEFT: 'TOPLEFT'>), row_span=2, col_span=1, start_row_offset_idx=0, 
end_row_offset_idx=2, start_col_offset_idx=5, end_col_offset_idx=6, text='پایه', column_header=True, 
row_header=False, row_section=False, fillable=False), TableCell(bbox=BoundingBox(l=239.59, t=256.796, r=347.845, 
b=268.41, coord_origin=<CoordOrigin.TOPLEFT: 'TOPLEFT'>), row_span=1, col_span=2, start_row_offset_idx=0, 
end_row_offset_idx=1, start_col_offset_idx=3, end_col_offset_idx=5, text='شرا حداقل ی فن طافراد یامتی آور از', 
column_header=True, row_header=False, row_section=False, fillable=False), TableCell(bbox=BoundingBox(l=155.193, 
t=249.95600000000002, r=191.898, b=320.85, coord_origin=<CoordOrigin.TOPLEFT: 'TOPLEFT'>), row_span=2, col_span=1, 
start_row_offset_idx=0, end_row_offset_idx=2, start_col_offset_idx=2, end_col_offset_idx=3, text='حداقل امتیاز 
کیفیت تجربه کاری شرکت', column_header=True, row_header=False, row_section=False, fillable=False), 
TableCell(bbox=BoundingBox(l=111.86, t=257.396, r=142.889, b=313.41, coord_origin=<CoordOrigin.TOPLEFT: 
'TOPLEFT'>), row_span=2, col_span=1, start_row_offset_idx=0, end_row_offset_idx=2, start_col_offset_idx=1, 
end_col_offset_idx=2, text='حداقل امتیاز امکانات پشتیبانی', column_header=True, row_header=False, 
row_section=False, fillable=False), TableCell(bbox=BoundingBox(l=76.944, t=264.716, r=97.78, b=305.97, 
coord_origin=<CoordOrigin.TOPLEFT: 'TOPL

[5] score=0.4542
text='نشر اداری\u200cها ۸۵ می\u200cباشد. گواهی صلاحیت حرفهای (در سه\u200cپایه؛ ۳) (، ۲) (و ۱) برای مدت ۴ سال صادر 
می\u200cشود که شرایط صدور آن (ها مطابق جدول شماره ۳) است. ماده ۷مرجع تشخیص صلاحیت مشاوران: تشخیص صلاحیت مشاوران از 
سوی سازمان صورت می\u200cگیرد. ماده ۸تعیین صلاحیت مشاوران: سازمان، مشاوران را در قالب ضوابط این دستورالعمل، در 
پایه\u200cهای (؛ ۳) (، ۲) (و ۱) در هر تخصص تعیین صلاحیت می\u200cکند. تبصره- هر مشاور می\u200cتواند با معرفی افراد 
واجد شرایط بر اساس ضوابط این دستورالعمل در یک، چند یا تمامی تخصصها تشخیص صلاحیت شود. حداقل شرط لازم برای این کار، 
معرفی ۳ نفر افراد امتیازآور به ازای هر تخصص می\u200cباشد. ماده ۹عوامل مؤثر بر رتبه بندی مشاوران عبارتند از: -نیروی 
انسانی متخصص (افراد امتیازآور). -کیفیت پروژه\u200cهای قبلی انجام شده توسط مشاور. -تجربه کاری مشاور -امکانات 
پشتیبانی ماده ۱۰شرایط عمومی' meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', 
doc_items=[TextItem(self_ref='#/texts/143', parent=RefItem(cref='#/body'), children=[], 
content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=20, 
bbox=BoundingBox(l=54.864, t=626.801990234375, r=399.969, b=114.26999023437497, 
coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 1603))], orig='نشر اداری\u200cها ۸۵ 
می\u200cباشد. گواهی صلاحیت حرفهای (در سه\u200cپایه؛ ۳) (، ۲) (و ۱) برای مدت ۴ سال صادر می\u200cشود که شرایط صدور آن
(ها مطابق جدول شماره ۳) است. ماده ۷مرجع تشخیص صلاحیت مشاوران: تشخیص صلاحیت مشاوران از سوی سازمان صورت می\u200cگیرد.
ماده ۸تعیین صلاحیت مشاوران: سازمان، مشاوران را در قالب ضوابط این دستورالعمل، در پایه\u200cهای (؛ ۳) (، ۲) (و ۱) در 
هر تخصص تعیین صلاحیت می\u200cکند. تبصره- هر مشاور می\u200cتواند با معرفی افراد واجد شرایط بر اساس ضوابط این 
دستورالعمل در یک، چند یا تمامی تخصصها تشخیص صلاحیت شود. حداقل شرط لازم برای این کار، معرفی ۳ نفر افراد امتیازآور به
ازای هر تخصص می\u200cباشد. ماده ۹عوامل مؤثر بر رتبه بندی مشاوران عبارتند از: -نیروی انسانی متخصص (افراد امتیازآور).
-کیفیت پروژه\u200cهای قبلی انجام شده توسط مشاور. -تجربه کاری مشاور -امکانات پشتیبانی ماده ۱۰شرایط عمومی رتبه بندی 
مشاوران: ۱-۱۰انجام خدمات مشاوره در اساسنامه شر کت قید و یا به تشخیص سازمان از مفاد اساسنامه شرکت قابل احراز باشد. 
تبصره: درخواست گواهی\u200cنامه خدمات مشاوره مدیریتی و بهره\u200cوری مراکز آموزشی و پژوهشی دولتی و غیردولتی (مانند 
دانشگاه\u200cها)؛ در صورت داشتن دانشکده، گروه آموزشی و یا پژوهشکده مرتبط با تخصصهای (مورد اشاره در جدول شماره ۱) 
دستورالعمل مورد بررسی قرار خواهند گرفت. (الحاقی به موجب بخشنامه شمار ه ۲۴۲۳۳۹ مورخ ۱۴/۵ / ۱۳۹۹) ۲-۱۰- به موارد 
مذکور در ماده ۲۰ قانون مجازات اسلامی محکوم نشده باشند. ۳-۱۰- دارا بودن مدر ک تحصیلی حداقل لیسانس یا معادل آن برای 
سهنفر افراد امتیازآور معرفی شده از سوی شرکت، مدیرعامل و اعضاء هیئت\u200cمدیره شرکت ضروری است. امتیاز افراد 
امتیازآور معرفیشده بر اساس موارد مندرج در جدول شماره ۲ محاسبه خواهد شد. ۴-۱۰- (دارا بودن شرایط مندرج در جدول شماره 
۳)', text='نشر اداری\u200cها ۸۵ می\u200cباشد. گواهی صلاحیت حرفهای (در سه\u200cپایه؛ ۳) (، ۲) (و ۱) برای مدت ۴ سال 
صادر می\u200cشود که شرایط صدور آن (ها مطابق جدول شماره ۳) است. ماده ۷مرجع تشخیص صلاحیت مشاوران: تشخیص صلاحیت 
مشاوران از سوی سازمان صورت می\u200cگیرد. ماده ۸تعیین صلاحیت مشاوران: سازمان، مشاوران را در قالب ضوابط این 
دستورالعمل، در پایه\u200cهای (؛ ۳) (، ۲) (و ۱) در هر تخصص تعیین صلاحیت می\u200cکند. تبصره- هر مشاور می\u200cتواند 
با معرفی افراد واجد شرایط بر اساس ضوابط این دستورالعمل در یک، چند یا تمامی تخصصها تشخیص صلاحیت شود. حداقل شرط لازم 
برای این کار، معرفی ۳ نفر افراد امتیازآور به ازای هر تخصص می\u200cباشد. ماده ۹عوامل مؤثر بر رتبه بندی مشاوران 
عبارتند از: -نیروی انسانی متخصص (افراد امتیازآور). -کیفیت پروژه\u200cهای قبلی انجام شده توسط مشاور. -تجربه کاری 
مشاور -امکانات پشتیبانی ماده ۱۰شرایط عمومی رتبه بندی مشاوران: ۱-۱۰انجام خدمات مشاوره در اساسنامه شر کت قید و یا به 
تشخیص سازمان از مفاد اساسنامه شرکت قابل احراز باشد. تبصره: درخواست گواهی\u200cنامه خدمات مشاوره مدیریتی و 
بهره\u200cوری مراکز آموزشی و پژوهشی دولتی و غیردولتی (مانند دانشگاه\u200cها)

In [40]:
from rich import print 

query = "رشته کامپیوتر"
results = hybrid_search(query, top_k=5, alpha=0.7)

for i, (chunk, score) in enumerate(results, 1):
    print(f"\n[{i}] score={score:.4f}\n{chunker.contextualize(chunk)}")


[1] score=0.3190
گروه‌بندی چهارم: هسته گزینش- دبیرخانه هیأت مرکزی گزینش
در گروهبندی مزبور، در یک واحد سازمانی تحت عنوان "برنامه‌ریزی، نوسازی و توسعه خدمات الکترونیکی" تجمیع شده و در 
دستگاه‌های سطح (الف) و (ب) زیر نظر معاونت توسعه مدیریت و منابع و در دستگاه‌های سطح (ج)، زیر نظر بالاترین مقام دستگاه
سازماندهی می‌شوند. تذکر ۱- در صورت ضرورت و نداشتن محدودیت تعداد واحدهای عمومی (سقف ٪۲۵ از کل واحدها) و نیز رعایت سقف
مقرر دربند (د) ماده ۲۹ قانون مدیریت خدمات کشوری، واحد فنآوری اطلاعات و ارتباطات می‌تواند به طور مستقل ایجاد شود. 
تذکر ۲- در صورتی که دستگاه عهدهدار وظایف برنامه‌ریزی تخصصی و موضوعی باشد، می توان "امور برنامه و بودجه"، "فنآوری 
اطلاعات و ارتباطات" و "آمار و اطلاعات" را نیز در معاونت مزبور و یا معاونتهای تخصصی مربوط دیگر سازماندهی نمود. تذکر 
۳- در صورتی که به دلیل رعایت نسبت تعداد

[2] score=0.3174
(بخشنامه شماره ۵۰۰۳۲ مورخ ۱۶/۰۷/۱۴۰۱ سازمان اداری و استخدامی کشور)
کارشناسی، نسبت به ایجاد و ابلاغ مشاغل تجمیعی جدید در مجتمع‌های اداری اقدام نماید.
میثم لطیفی
نشر اداری‌ها
۸۳۱

[3] score=0.3173
(بخشنامه شماره ۴۹۳۸۱ مورخ ۱۱/۰۷/۱۴۰۱ سازمان اداری و استخدامی کشور)
-مقابله با حوادث و حملات فضای مجازی؛ -تحلیل، ارزیابی و مدیریت مخاطرات؛ -اجرای آزمون، مانور و تست نفوذ؛ -ایجاد ساز و
کار ثبت وقایع امنیت اطلاعات و رصد وقایع و رویدادهای سایبری؛ -تهیه دستورالعمل‌ها و آگاهی‌های امنیتی آموزشی جهت ارتقاء
آگاهی کارکنان با همکاری واحدهای متولی امنیت سایبری در سطح ملی؛ -اجرای الزامات و ضوابط ابلاغی توسط مراجع ذیصلاح در 
سطح ملی؛ تبصره: واحدهای متولی فناوری اطلاعات در دستگاه‌ها ی اجرایی که وظایف دیگری به غیراز فناوری اطلاعات بر عهدهدار
ند (از قبیل نوسازی اداری، تشکیلات و. .) به عناوین آنها عبارت "امنیت فضای مجازی" و به وظایف آنها وظایف مرتبط اضافه 
می‌گردد. ۳- در وزارتخانه‌ها و سازمان‌های مستقل ذیل رییسجمهور یک

[4] score=0.3151
د- شیوه اجرا:
ارتباطات (فنآوری اطلاعات، ارتباطات و تحول اداری- فنآوری اطلاعا ت) و ارتباطات، توسعه خدمات الکترونیکی ۱۷توسعه سرمایه
انسانی (توسعه منابع انسانی، امور اداری،) کارگزینی، استخدام، آموزش، بهسازی، بیمه و رفاه کارکنان ۱۸- پشتیبانی (تدار 
کات و خدمات، پشتیبانی) و خدمات فنی/ اداری/ رفاهی ۱۹امور مالی (امور مالی، امور مالی و ذی) حسابی ۲۰دبیرخانه ها و سایر
فعالیتهای خدمات عمومی دیگر. ۷گروهبندی وظایف و فعالیتهای عمومی و تعیین جایگاه واحد و یا واحدهای سازمانی عهده‌دار این
وظایف که با توجه به تجانس و همسو بودن آنها و به دلیل رعایت نسبت تعداد واحدهای عمومی به کل واحدها (ح داکثر ٪۲۵) 
قابلیت ادغام با همدیگر را دارند، به شرح زیر است: الف- گروه‌بندی وظایف و فعالیت‌های عمومی زیر نظر وزیر/ رییس و یا 
بالاترین مقام دستگاه:
نشر اداری‌ها

[5] score=0.3119
(بخشنامه شماره ۴۹۳۸۱ مورخ ۱۱/۰۷/۱۴۰۱ سازمان اداری و استخدامی کشور)
پست معاونت در واحدهای "فناوری اطلاعات و امنیت فضای مجازی" با عنوان "معاون امنیت" ایجاد می‌گردد. تبصره: معاون امنیت 
در دستگاه‌های اجرایی مشمول این ماده در رده مشاغل حساس قرار می‌گیرد. ۴به منظور مدیریت یکپارچه امنیت فضای مجازی "کمیته
راهبری امنیت اطلاعات" به ریاست بالاترین مقام دستگاه اجرایی یا معاون وی با عضویت بالاترین مسئول حوزه فناوری اطلاعات 
و امنیت فضای مجازی و بالاترین مقام مسئول حراست ایجاد می‌گردد و تصمیمات آن در سطح دستگاه اجرایی لازم الاجر ا می‌باشد.
دبیرخانه این کمیته در واحد فناوری اطلاعات و امنیت فضای مجازی دستگاه اجرایی مستقر می‌باشد.
جمشید انصاری

In [41]:
def get_clean_chunk(chunk):
    items = []
    for doc_item in chunk.meta.doc_items:
        items.append({
            "label": doc_item.label,
            "page_number": doc_item.prov[0].page_no,
            "charspan": doc_item.prov[0].charspan
         })
                
    clean_chunk = {
        "meta": {"filename": chunk.meta.origin.filename, "headings": chunk.meta.headings},
        "text": chunk.text
    }
    if items:
        clean_chunk["meta"]["chunk_items"] = items

    return clean_chunk

In [ ]:
from rich import print
from ollama import chat  # or any LLM API you use, e.g., OpenAI, HuggingFace
import json

def augment_prompt(related_chunks):
    # Combine retrieved texts for LLM input
    context_texts = []
    for i, (chunk, score) in enumerate(related_chunks, 1):
        context_texts.append(str(get_clean_chunk(chunk)))

    # ---- Prepare Context ----
    context = "\n\n---\n\n".join(context_texts)

    # ---- LLM Generation ----
    prompt = f"""
    سؤال کاربر:
    {query}

    تو یک دستیار هوشمند برای پاسخ‌دهی به پرسش‌ها بر اساس اسناد بازیابی‌شده هستی.
    فقط و فقط بر اساس متن‌های داده‌شده پاسخ بده.

    اگر پاسخ در متن‌ها وجود نداشت، حتماً فقط بنویس:
    «پاسخی یافت نشد.»

    وظایف:

    محتوای پرسش را بفهم و فقط بر اساس بخش‌های متنی ارائه‌شده پاسخ بده.

    هیچ دانش بیرونی، حدسی یا استنباط فراتر از متن مجاز نیست.

    در پاسخ نهایی، منبع را با این فرمت ذکر کن:
    
    نام heading (اگر وجود دارد)

    شماره صفحه (page_number از JSON)

    متن‌های بازیابی‌شده  قالب json:
    {context}
    """
    return prompt


# ---- Retrieval ----
query = "شرایط عمومی احراز صلاحیت افراد امتیازآور"
related_chunks = hybrid_search(query, top_k=5, alpha=0.7)
prompt = augment_prompt(related_chunks)
print(prompt)

# # Example with Ollama (local model)
response = chat(model="Gemma3:12b", messages=[{"role": "user", "content": prompt}])

# # ---- Display ----
print("\n[bold green]Answer:[/bold green]\n")
print(response['message']['content'])


سؤال کاربر:
    شرایط عمومی احراز صلاحیت افراد امتیازآور

    تو یک دستیار هوشمند برای پاسخ‌دهی به پرسش‌ها بر اساس اسناد بازیابی‌شده هستی.
    فقط و فقط بر اساس متن‌های داده‌شده پاسخ بده.

    اگر پاسخ در متن‌ها وجود نداشت، حتماً فقط بنویس:
    «پاسخی یافت نشد.»

    وظایف:

    محتوای پرسش را بفهم و فقط بر اساس بخش‌های متنی ارائه‌شده پاسخ بده.

    هیچ دانش بیرونی، حدسی یا استنباط فراتر از متن مجاز نیست.

    در پاسخ نهایی، منبع را با این فرمت ذکر کن:

    نام heading (اگر وجود دارد)

    شماره صفحه (page_number از JSON)

    متن‌های بازیابی‌شده  قالب json:
    {'meta': {'filename': 'chapter02-05.pdf', 'headings': ['فصل دوم: صلاحیت حرفه\u200cای افراد امتیازآور'], 
'chunk_items': [{'label': <DocItemLabel.TEXT: 'text'>, 'page_number': 18, 'charspan': (0, 48)}, {'label': 
<DocItemLabel.LIST_ITEM: 'list_item'>, 'page_number': 18, 'charspan': (0, 47)}, {'label': <DocItemLabel.LIST_ITEM: 
'list_item'>, 'page_number': 18, 'charspan': (0, 113)}, {'label': <DocItemLabel.LIST_ITEM: 'list_item'>, 
'page_number': 18, 'charspan': (0, 68)}, {'label': <DocItemLabel.LIST_ITEM: 'list_item'>, 'page_number': 18, 
'charspan': (0, 95)}, {'label': <DocItemLabel.LIST_ITEM: 'list_item'>, 'page_number': 18, 'charspan': (0, 149)}]}, 
'text': 'ماده ۴شرایط عمومی احراز صلاحیت افراد امتیازآور:\n- ۱-۴- تابعیت جمهوری اسلامی ایران را داشته باشد.\n- ۲-۴- 
دارای مدر ک تحصیلی حداقل لیسانس یا معادل آن مرتبط با تخصص و رشته\u200cها تحصیلی مورد نظر طبق جدول شماره ۱ باشد.\n- 
۳-۴- محروم از حقوق اجتماعی موضوع ماده ۲۶ قانون مجازات اسلامی نباشد.\n- ۴-۴- رابطه استخدامی (رسمی، پیمانی، قراردادی 
و عناوین مشابه) با دستگاه\u200cهای اجرایی نداشته باشد.\n- ۴-۵ممنوعیت مداخله در معاملات دولتی، موضوع لایحه قانونی 
راجع به منع مداخله وزرا، نمایندگان مجلس و کارمندان دولت در معاملات دولتی و کشوری نداشته باشد.'}

---

{'meta': {'filename': 'chapter02-05.pdf', 'headings': ['فصل دوم: صلاحیت حرفه\u200cای افراد امتیازآور'], 
'chunk_items': [{'label': <DocItemLabel.TEXT: 'text'>, 'page_number': 18, 'charspan': (0, 293)}, {'label': 
<DocItemLabel.TEXT: 'text'>, 'page_number': 18, 'charspan': (0, 155)}, {'label': <DocItemLabel.TEXT: 'text'>, 
'page_number': 18, 'charspan': (0, 50)}, {'label': <DocItemLabel.TEXT: 'text'>, 'page_number': 18, 'charspan': (0, 
132)}]}, 'text': 'تبصره ۱: برای افراد امتیازآور معرفی شده از سوی مراکز آموزشی و پژوهشی دولتی و غیردولتی، داشتن مدر 
ک تحصیلی دکتری با درجه علمی حداقل دانشیار در رشته\u200cهای مرتبط با تخصص و رشته\u200cهای تحصیلی (مندرج در جدول ۱) 
بخشنامه الزامی می\u200cباشد. (الحاقی به موجب بخشنامه شماره ۲۴۲۳۳۹ مورخ ۱۴ / ۵/۱۳۹۹)\nتبصره ۲: رعایت بندهای ۴ -۴ و 
۴-۵ برای افراد امتیازآور معرفی شده از سوی مراکز دولتی، الزامی نیست. (الحاقی به موجب بخشنامه شماره ۲۴۲۳۳۹ مورخ ۱۴/۵ 
/ ۱۳۹۹)\nماده ۵شرایط اختصاصی احراز صلاحیت افراد امتیازآور:\n۱-۵- تعیین امتیاز حرفه\u200cای افراد امتیازآور بر اساس 
جدول ۲ و با توجه به پایه و تخصص مورد تقاضا توسط شر کت مورد محاسبه قرار می\u200cگیرد.'}

---

{'meta': {'filename': 'chapter02-05.pdf', 'headings': ['ماده ۳تعاریف:'], 'chunk_items': [{'label': 
<DocItemLabel.TEXT: 'text'>, 'page_number': 17, 'charspan': (0, 192)}, {'label': <DocItemLabel.TEXT: 'text'>, 
'page_number': 17, 'charspan': (0, 129)}, {'label': <DocItemLabel.TEXT: 'text'>, 'page_number': 17, 'charspan': (0,
210)}]}, 'text': '۸-۳- فرد امتیازآور: کارشناسی است که حداقل امتیاز حرفه\u200cای لازم از مندرجات جدول شماره ۲ برای 
پایه مورد نظر را کسب نموده و فعالیتهای مرتبط با تخصص مورد تقاضا را با همکاری گروه به عهده\u200cدار د.\n۹-۳- گروه: 
دربر گیرنده افرادی با عناوین سر گروه و امتیازآوران می\u200cباشند که\u200cبرای انجام خدمات مشاوره\u200cای در یک تخصص
تشکیل شده\u200cاست.\n۱۰-۳سر گروه: کارشناسی که دارای حداقل امتیاز حرفهای لازم از مندرجات جدول شماره ۲ برای پایه مورد
نظر و سایر شرایط لازم بوده و سرپرستی فعالیت\u200cهای مشاوره\u200cای مربوط به تخصص مورد تقاضا را در شر کت برعهده 
داشته باشد.'}

---

{'meta': {'filename': 'chapter02-05.pdf', 'headings': ['ماده ۱۱امتیاز مربوط به کیفیت تجربه کاری شرکت متقاضی تشخیص 
صلاحیت:'], 'chunk_items': [{'label': <DocItemLabel.TEXT: 't

Answer:

شرایط عمومی احراز صلاحیت افراد امتیازآور:

- ۱-۴- تابعیت جمهوری اسلامی ایران را داشته باشد.
- ۲-۴- دارای مدرک تحصیلی حداقل لیسانس یا معادل آن مرتبط با تخصص و رشته‌های تحصیلی مورد نظر طبق جدول شماره ۱ باشد.
- ۳-۴- محروم از حقوق اجتماعی موضوع ماده ۲۶ قانون مجازات اسلامی نباشد.
- ۴-۴- رابطه استخدامی (رسمی، پیمانی، قراردادی و عناوین مشابه) با دستگاه‌های اجرایی نداشته باشد.
- ۴-۵ ممنوعیت مداخله در معاملات دولتی، موضوع لایحه قانونی راجع به منع مداخله وزرا، نمایندگان مجلس و کارمندان دولت 
در معاملات دولتی و کشوری نداشته باشد.

فصل دوم: صلاحیت حرفه‌ای افراد امتیازآور
page_number: 18